# Langton's Ant implementation with OOP

## Class Definition


In [1]:
SQUARE_SIZE = 6
BOARD_X = 151
BOARD_Y = 91
ANT_SIZE = 3

In [2]:
class Square:
    def __init__(self, size, px, py):
        self.size = size
        self.color = 'white'
        self.px = px
        self.py = py

    def toggle_color(self):
        if self.color == 'white':
            self.color = 'black'
            return
        self.color = 'white'

    def __mul__(self, other):
        if isinstance(other, int):
            return [self for _ in range(other)]
        else:
            raise NotImplemented

    def rect(self):
        return '<rect x="{px}" y="{py}" width="{x}" height="{x}" stroke="black" stroke-width="1" fill="{c}"/>'.format(
            px=self.px, py=self.py, x=self.size, c=self.color)

In [3]:
class Board:
    def __init__(self, x, y):
        self.x = x
        self.y = y
        self.grid = {}
        for i in range(y):
            self.grid[i] = {}
            for j in range(x):
                self.grid[i][j] = Square(SQUARE_SIZE, SQUARE_SIZE * j, SQUARE_SIZE * i)

    def svg(self, ant):
        return """
        <svg width='{x}' height='{y}' style='background: #f7f7f9'>
        """.format(x=self.x * SQUARE_SIZE, y=self.y * SQUARE_SIZE) + """
        {}
        </svg>""".format(
            "\n".join("".join(v.rect() for v in self.grid[row].values()) for row in self.grid.keys()) + ant.svg())

    def draw(self):
        pass

In [4]:
class Ant:
    def __init__(self, size, speed, x, y):
        self.size = size
        self.speed = speed
        self.x = x
        self.y = y
        self.direction = 1

    def svg(self):
        return '<circle cx="{px}" cy="{py}" r="{s}" stroke="black" stroke-width="1" fill="red" />'.format(
            px=self.x * SQUARE_SIZE - SQUARE_SIZE / 2, py=self.y * SQUARE_SIZE - SQUARE_SIZE / 2, s=self.size)

    def langton_direction(self, board):
        if board.grid[self.y - 1][self.x - 1].color == 'white':
            self.direction += 1
            if self.direction > 4:
                self.direction = 1
            return
        self.direction -= 1
        if self.direction < 1:
            self.direction = 4

    def paint_square(self, board):
        board.grid[self.y - 1][self.x - 1].toggle_color()

    def move(self, board):
        self.langton_direction(board)
        if self.direction == 1:
            self.x += 1
        if self.direction == 2:
            self.y += 1
        if self.direction == 3:
            self.x -= 1
        if self.direction == 4:
            self.y -= 1
        if self.x < 1:
            self.x = BOARD_X
        if self.y < 1:
            self.y = BOARD_Y
        if self.x > BOARD_X:
            self.x = 1
        if self.y > BOARD_Y:
            self.y = 1

## Creating objects

In [5]:
board = Board(BOARD_X, BOARD_Y)
ant = Ant(ANT_SIZE, 1, BOARD_X // 2, BOARD_Y // 2)

## Main loop

In [6]:
from IPython.display import clear_output, display, HTML

def main_loop(n):
    for i in range(n):
        ant.move(board)
        ant.paint_square(board)

## Stages

### Phase 1: Chaotic growth 

In [7]:
main_loop(10000)

In [8]:
display(HTML(board.svg(ant)))
clear_output(wait=True)

### Phase 2: Emergent order 

In [9]:
main_loop(1500)

In [10]:
display(HTML(board.svg(ant)))
clear_output(wait=True)

### Phase 3: Connected tunnels

Since the ant can loop around the borders, the tunnels end up connecting.

In [11]:
main_loop(35000)

In [12]:
display(HTML(board.svg(ant)))
clear_output(wait=True)

### Phase 4: Very large loop 

Due to space limitation, the will walk all squares when the number of loops is too large, and then it goes back to chaotic form.

In [13]:
main_loop(160000)

In [14]:
display(HTML(board.svg(ant)))
clear_output(wait=True)